In [1]:
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)
import socket
import numpy as np
%matplotlib notebook
import matplotlib
from matplotlib.pyplot import imshow
import matplotlib.pyplot as plt
%matplotlib inline
import time
import PIL
import io
import ctypes as c
import pandas as pd
import tensorflow as tf
from tensorflow import keras
from keras.models import load_model
from keras.preprocessing import image
from matplotlib import pyplot as plt
from multiprocessing import Pool, Value, Array #Process causes a hang?!
from ipywidgets import *
import ipywidgets as widgets
from functools import partial
#from ipyleaflet import Map, Heatmap
import dask
import IPython.display
from dask_jobqueue import SLURMCluster
from dask.distributed import Client
import dask.array as da
from concurrent.futures import ProcessPoolExecutor
from shutil import copyfile

from IPython.display import clear_output
host=socket.gethostname()
print(host)

Using TensorFlow backend.


farm180301.jlab.org


In [2]:
img_to_judge_loc="/u/home/tbritton/Jupyter/MLChallenge3/"+"POTQ_03_TENNANT_B.png" ###CHANGE THIS

In [3]:
MODEL="./CDC_occupancy-1569856232_566866.h5"
TARGET_img_loc=""+"TARGET_IMG.png"

MODEL_LABELS=["Bad","Good","NoData"]

target_img = PIL.Image.open(TARGET_img_loc)
img_to_judge = PIL.Image.open(img_to_judge_loc)

target_Arr = np.asarray( target_img, dtype="int32" )
submit_Arr = np.asarray( img_to_judge, dtype="int32" )

In [4]:
%%capture
model=load_model(MODEL);
to_pred=pd.DataFrame(columns=["datum"])
        
to_pred=to_pred.append({"datum":TARGET_img_loc}, ignore_index=True)
to_pred=to_pred.append({"datum":img_to_judge_loc}, ignore_index=True)

test_datagen = tf.keras.preprocessing.image.ImageDataGenerator(rescale=1./255)
test_generator = test_datagen.flow_from_dataframe(
            dataframe=to_pred,
            directory=None,
            x_col="datum",
            target_size=(model.layers[0].input_shape[1],model.layers[0].input_shape[2]),
            color_mode="rgb",
            batch_size=1,
            class_mode=None,
            shuffle=False
        )
preds=model.predict_generator(test_generator,verbose=1,steps=test_generator.n)

In [5]:
target_pred=preds[0]
submit_pred=preds[1]

In [6]:
targ_verdict_index=np.where(target_pred==np.amax(target_pred))[0]
targ_verdict_confidence=np.amax(target_pred)

submit_verdict_index=np.where(submit_pred==np.amax(submit_pred))[0]
submit_verdict_confidence=np.amax(submit_pred)

In [7]:
if(targ_verdict_index[0]==0):
    targ_verdict_confidence*=-1
    
if(submit_verdict_index[0]==0):
    submit_verdict_confidence*=-1

In [8]:
CONFIDENCE_DELTA=submit_verdict_confidence-targ_verdict_confidence

In [9]:
difference_sum=0.
for y in range(0,target_Arr.shape[0]):
    for x in range(0,target_Arr.shape[1]):
        for c in range(0,target_Arr.shape[2]):
            delta=submit_Arr[y][x][c]-target_Arr[y][x][c]
            difference_sum+=abs(delta)

In [10]:
imgbytearr=io.BytesIO()
target_img.save(imgbytearr,format='PNG')

subimgbytearr=io.BytesIO()
img_to_judge.save(subimgbytearr,format='PNG')

imgs=[]

targetIMG=widgets.Image(value=imgbytearr.getvalue(),width=target_Arr.shape[1],height=target_Arr.shape[0])
imgs.append(targetIMG)

submitIMG=widgets.Image(value=subimgbytearr.getvalue(),width=submit_Arr.shape[1],height=submit_Arr.shape[0])
imgs.append(submitIMG)

display(widgets.HBox(imgs))

if target_Arr.shape != submit_Arr.shape:
    print("%s is of the wrong shape and thus disqualified" % img_to_judge_loc)
elif CONFIDENCE_DELTA==0:
    print("%s is an unmodified image and disqualified" % img_to_judge_loc)
else:
    print("Change in confidence: %f" % CONFIDENCE_DELTA)
    print("SCORE FOR %s is %f" % (img_to_judge_loc,float(difference_sum)/CONFIDENCE_DELTA))

Change in confidence: 1.596330
SCORE FOR /u/home/tbritton/Jupyter/MLChallenge3/POTQ_03_TENNANT_B.png is 8477278.912747
